В этом ноутбуке мы попытаемся прогнозировать данные по транзакциям с использованием библиотеки пророк

Загрузим библиотеки и данные

In [2]:
# Load libraries
import numpy as np
RANDOM_SEED = 42
np.random.seed(RANDOM_SEED)
import pandas as pd
pd.set_option('display.max_rows', 10)
pd.set_option('display.max_columns', 70)
import plotly.offline as py
import plotly.graph_objs as go
py.init_notebook_mode()

from fbprophet import Prophet

%time df_transactions = pd.read_csv('data/transactions.csv')
%time df_holidays_events = pd.read_csv('data/holidays_events.csv')

print('Data and libraries are loaded.')

CPU times: user 23 ms, sys: 8.86 ms, total: 31.8 ms
Wall time: 29.4 ms
CPU times: user 2.93 ms, sys: 552 µs, total: 3.48 ms
Wall time: 3.27 ms
Data and libraries are loaded.


In [3]:
#conda install fbprophet

In [4]:
df_transactions

date  store_nbr  transactions
0      2013-01-01         25           770
1      2013-01-02          1          2111
2      2013-01-02          2          2358
3      2013-01-02          3          3487
4      2013-01-02          4          1922
...           ...        ...           ...
83483  2017-08-15         50          2804
83484  2017-08-15         51          1573
83485  2017-08-15         52          2255
83486  2017-08-15         53           932
83487  2017-08-15         54           802

[83488 rows x 3 columns]

Если мы посмотрим на данные транзакций, транзакции сгруппированы по номерам магазинов. Сейчас мы упростим это и сгруппируем их по дате. 

In [5]:
transactions = df_transactions.groupby('date')['transactions'].sum()
py.iplot([go.Scatter(
    x=transactions.index,
    y=transactions
)])

Хорошо заметно влияние сезонности и праздников на общий объем транзакций.

Теперь давайте попробуем библиотеку пророк и посмотрим, насколько хорошо она предсказывает. Но перед этим мы должны подготовить данные. Согласно документации:

> Prophet следует API модели sklearn. Мы создаем экземпляр класса Prophet, а затем вызываем его методы соответствия и прогнозирования.
> Входными данными для Prophet всегда является фрейм данных с двумя столбцами: ** ds ** и ** y **. Столбец ds (отметка даты) должен содержать дату или дату и время (это нормально). Столбец ** y ** должен быть числовым и представлять измерение, которое мы хотим спрогнозировать.

In [7]:
transactions = pd.DataFrame(transactions).reset_index()
transactions.columns = ['ds', 'y']
transactions

ds      y
0     2013-01-01    770
1     2013-01-02  93215
2     2013-01-03  78504
3     2013-01-04  78494
4     2013-01-05  93573
...          ...    ...
1677  2017-08-11  89551
1678  2017-08-12  89927
1679  2017-08-13  85993
1680  2017-08-14  85448
1681  2017-08-15  86561

[1682 rows x 2 columns]

In [8]:
m = Prophet()
m.fit(transactions)
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)
forecast

INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.


ds         trend    yhat_lower     yhat_upper   trend_lower  \
0    2013-01-01  77909.076156  76333.602537   96097.557543  77909.076156   
1    2013-01-02  77919.018227  74486.518561   95467.196384  77919.018227   
2    2013-01-03  77928.960298  68864.121674   89108.054637  77928.960298   
3    2013-01-04  77938.902368  72724.463974   93253.944117  77938.902368   
4    2013-01-05  77948.844439  85098.183291  106443.560713  77948.844439   
...         ...           ...           ...            ...           ...   
2042 2018-08-11  97073.167349  96587.962390  116785.714443  96116.528226   
2043 2018-08-12  97089.681523  91215.309125  111474.509084  96127.911932   
2044 2018-08-13  97106.195698  80899.175366  102060.792824  96139.295637   
2045 2018-08-14  97122.709872  78829.527393   99248.064933  96150.679343   
2046 2018-08-15  97139.224047  81050.120007  101041.808950  96162.063048   

       trend_upper  additive_terms  additive_terms_lower  \
0     77909.076156     8039.042619           8039.042619   
1     77919.018227     7132.554272           7132.554272   
2     77928.960298     1622.621343           1622.621343   
3     77938.902368     5206.485764           5206.485764   
4     77948.844439    17882.474809          17882.474809   
...            ...             ...                   ...   
2042  98169.763493     9936.243023           9936.243023   
2043  98191.315292     4534.975842           4534.975842   
2044  98213.705084    -6008.793534          -6008.793534   
2045  98234.318882    -7744.566748          -7744.566748   
2046  98254.370873    -6529.126348          -6529.126348   

      additive_terms_upper        weekly  weekly_lower  weekly_upper  \
0              8039.042619  -4840.291158  -4840.291158  -4840.291158   
1              7132.554272  -3740.976526  -3740.976526  -3740.976526   
2              1622.621343  -7236.379219  -7236.379219  -7236.379219   
3              5206.485764  -1661.074267  -1661.074267  -1661.074267   
4             17882.474809  12952.721155  12952.721155  12952.721155   
...                    ...           ...           ...           ...   
2042           9936.243023  12952.721155  12952.721155  12952.721155   
2043           4534.975842   7553.492502   7553.492502   7553.492502   
2044          -6008.793534  -3027.492488  -3027.492488  -3027.492488   
2045          -7744.566748  -4840.291158  -4840.291158  -4840.291158   
2046          -6529.126348  -3740.976526  -3740.976526  -3740.976526   

            yearly  yearly_lower  yearly_upper  multiplicative_terms  \
0     12879.333777  12879.333777  12879.333777                   0.0   
1     10873.530798  10873.530798  10873.530798                   0.0   
2      8859.000562   8859.000562   8859.000562                   0.0   
3      6867.560031   6867.560031   6867.560031                   0.0   
4      4929.753654   4929.753654   4929.753654                   0.0   
...            ...           ...           ...                   ...   
2042  -3016.478132  -3016.478132  -3016.478132                   0.0   
2043  -3018.516659  -3018.516659  -3018.516659                   0.0   
2044  -2981.301047  -2981.301047  -2981.301047                   0.0   
2045  -2904.275591  -2904.275591  -2904.275591                   0.0   
2046  -2788.149822  -2788.149822  -2788.149822                   0.0   

      multiplicative_terms_lower  multiplicative_terms_upper           yhat  
0                            0.0                         0.0   85948.118775  
1                            0.0                         0.0   85051.572499  
2                            0.0                         0.0   79551.581641  
3                            0.0                         0.0   83145.388132  
4                            0.0                         0.0   95831.319248  
...                          ...                         ...            ...  
2042                         0.0                         0.0  107009.410372  
2043                     

In [9]:
py.iplot([
    go.Scatter(x=transactions['ds'], y=transactions['y'], name='y'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat'], name='yhat'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_upper'], fill='tonexty', mode='none', name='upper'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_lower'], fill='tonexty', mode='none', name='lower'),
    go.Scatter(x=forecast['ds'], y=forecast['trend'], name='Trend')
])

In [10]:
# Вычислим среднеквадратичную ошибку.
print('RMSE: %f' % np.sqrt(np.mean((forecast.loc[:1682, 'yhat']-transactions['y'])**2)) )

RMSE: 7903.188084


Как видно на графике выше, прогноз довольно хороший и согласуется с взлетами и падениями данных. Вы можете увеличить график, выбрав область масштабирования с помощью мыши.

Но тенденция довольно жесткая, она не учитывает под-тренды середины года. В первой половине года тенденция нарастает, а затем немного замедляется. Сделаем тренд немного гибким. Если тренд является переобученным (слишком большая гибкость) или недостаточными (недостаточная гибкость), вы можете отрегулировать силу разреженности перед использованием входного аргумента ** changepoint_prior_scale **. По умолчанию этот параметр установлен на 0,05. Его увеличение сделает тренд более гибким. (https://facebook.github.io/prophet/docs/trend_changepoints.html)

In [11]:
m = Prophet(changepoint_prior_scale=2.5)
m.fit(transactions)
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)

INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.


In [12]:
# Вычислим среднеквадратичную ошибку.
print('RMSE: %f' % np.sqrt(np.mean((forecast.loc[:1682, 'yhat']-transactions['y'])**2)) )
py.iplot([
    go.Scatter(x=transactions['ds'], y=transactions['y'], name='y'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat'], name='yhat'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_upper'], fill='tonexty', mode='none', name='upper'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_lower'], fill='tonexty', mode='none', name='lower'),
    go.Scatter(x=forecast['ds'], y=forecast['trend'], name='Trend')
])

RMSE: 7860.811204


Теперь добавим в модель больше сезонности. Как мы видим, Пророк рассчитывает еженедельную и годовую сезонность. Нам не нужна ежедневная сезонность, потому что у нас нет внутридневных данных для этого случая. Достаточно просто добавить ежемесячную сезонность.

In [13]:
m = Prophet(changepoint_prior_scale=2.5)
m.add_seasonality(name='monthly', period=30.5, fourier_order=5)
m.fit(transactions)
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)

INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.


In [14]:
# Вычислим среднеквадратичную ошибку.
print('RMSE: %f' % np.sqrt(np.mean((forecast.loc[:1682, 'yhat']-transactions['y'])**2)) )
py.iplot([
    go.Scatter(x=transactions['ds'], y=transactions['y'], name='y'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat'], name='yhat'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_upper'], fill='tonexty', mode='none', name='upper'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_lower'], fill='tonexty', mode='none', name='lower'),
    go.Scatter(x=forecast['ds'], y=forecast['trend'], name='Trend')
])

RMSE: 7681.506809


Пришло время добавить в нашу модель влияние праздников. Сначала нам нужно настроить формат данных. Пророку нужны два столбца (праздник и ds) и строка для каждого наступления праздника. Так же можно включить столбцы lower_window и upper_window, которые продлевают праздничные дни до дней «[lower_window, upper_window]» вокруг даты. 

In [15]:
df_holidays_events

date        type    locale locale_name  \
0    2012-03-02     Holiday     Local       Manta   
1    2012-04-01     Holiday  Regional    Cotopaxi   
2    2012-04-12     Holiday     Local      Cuenca   
3    2012-04-14     Holiday     Local    Libertad   
4    2012-04-21     Holiday     Local    Riobamba   
..          ...         ...       ...         ...   
345  2017-12-22  Additional  National     Ecuador   
346  2017-12-23  Additional  National     Ecuador   
347  2017-12-24  Additional  National     Ecuador   
348  2017-12-25     Holiday  National     Ecuador   
349  2017-12-26  Additional  National     Ecuador   

                       description  transferred  
0               Fundacion de Manta        False  
1    Provincializacion de Cotopaxi        False  
2              Fundacion de Cuenca        False  
3        Cantonizacion de Libertad        False  
4        Cantonizacion de Riobamba        False  
..                             ...          ...  
345                      Navidad-3        False  
346                      Navidad-2        False  
347                      Navidad-1        False  
348                        Navidad        False  
349                      Navidad+1        False  

[350 rows x 6 columns]

In [16]:
holidays = df_holidays_events[df_holidays_events['transferred'] == False][['description', 'date']]
holidays.columns = ['holiday', 'ds']
#holidays['lower_window'] = 0
#holidays['upper_window'] = 0
holidays

holiday          ds
0               Fundacion de Manta  2012-03-02
1    Provincializacion de Cotopaxi  2012-04-01
2              Fundacion de Cuenca  2012-04-12
3        Cantonizacion de Libertad  2012-04-14
4        Cantonizacion de Riobamba  2012-04-21
..                             ...         ...
345                      Navidad-3  2017-12-22
346                      Navidad-2  2017-12-23
347                      Navidad-1  2017-12-24
348                        Navidad  2017-12-25
349                      Navidad+1  2017-12-26

[338 rows x 2 columns]

In [17]:
m = Prophet(changepoint_prior_scale=2.5, holidays=holidays)
m.add_seasonality(name='monthly', period=30.5, fourier_order=5)
m.fit(transactions)
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)

INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.


In [18]:
# Вычислим среднеквадратичную ошибку.
print('RMSE: %f' % np.sqrt(np.mean((forecast.loc[:1682, 'yhat']-transactions['y'])**2)) )
py.iplot([
    go.Scatter(x=transactions['ds'], y=transactions['y'], name='y'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat'], name='yhat'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_upper'], fill='tonexty', mode='none', name='upper'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_lower'], fill='tonexty', mode='none', name='lower'),
    go.Scatter(x=forecast['ds'], y=forecast['trend'], name='Trend')
])

RMSE: 4929.575239


Нам удалось спрогнозировать всплески на новогодний период. Модель не смогла уловить резкий скачок вниз на 4 января 2016 года, поэтому она не смогла успешно спрогнозировать 1 января 2017 года. 
Это объясняется тем, что 4 января 2016 года не было выходных. Но модель хорошо предсказывает продажи на 24 декабря. А также прогнозируемый период после 15 августа 2017 года выглядит неплохо.


Prophet - это довольно простая в использовании библиотека для прогнозирования данных временных рядов, которая использует для этого только предыдущие данные и праздники. Есть другие функции и параметры, такие как прогнозы насыщения, интервалы неопределенности и т. Д., Которые мы здесь не рассматривали. Вы можете прочитать больше в статье https://peerj.com/preprints/3190.pdf.